In [12]:
pip install transformers datasets huggingface_hub sentence-transformers

In [13]:
import re
import nltk
from nltk.corpus import stopwords
import torch
from torch.utils.data import DataLoader, TensorDataset
from transformers import AutoTokenizer, AutoModelForMaskedLM, AdamW
import pandas as pd
from tqdm import tqdm

In [14]:
# Load your unlabeled dataset
resumes = pd.read_csv('/content/MyResume2.csv')

In [15]:
resumes.head(5)

Resumes
0  Global Sales Administrator Biamp Systems Globa...
1  Python Developer <span class="hl">Python</span...
2  IT Project Manager <span class="hl">IT</span> ...
3  UI Front End Developer UI <span class="hl">Fro...
4  IT Security Analyst <span class="hl">IT</span>...

In [16]:
# Define the function for cleaning text
def clean_text(text):
    return re.sub(r"<span class=\"hl\">(.*?)</span>", r"\1", text)
# Apply the function to the entire column
resumes['Resumes'] = resumes['Resumes'].apply(clean_text)

In [17]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [18]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [19]:
def clean_resume(resume):
    if isinstance(resume, str):
        # Convert to lowercase
        resume = resume.lower()

        # Remove URLs, RT, cc, hashtags, mentions, non-ASCII characters, punctuation, and extra whitespace
        resume = re.sub('http\S+\s*|RT|cc|#\S+|@\S+|[^\x00-\x7f]|[^\w\s]', ' ', resume)
        resume = re.sub('\s+', ' ', resume).strip()

        return resume
    else:
        return ''

# Applying the cleaning function to a Datasets
resumes['Resumes']  = resumes['Resumes'].apply(lambda x: clean_resume(x))

In [ ]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForMaskedLM, AdamW
import torch
from torch.utils.data import DataLoader, TensorDataset
from tqdm import tqdm

# Load the pre-trained model
mpnet = "sentence-transformers/all-mpnet-base-v2"
tokenizer = AutoTokenizer.from_pretrained(mpnet)
pretrained_model = AutoModelForMaskedLM.from_pretrained(mpnet)

# Assuming 'resumes' is a DataFrame with a column named 'Resumes'
texts = resumes['Resumes'].tolist()

# Tokenize and encode the unlabeled data
encodings = tokenizer(texts, padding=True, truncation = True, return_tensors='pt')

# Create a TensorDataset
dataset = TensorDataset(encodings['input_ids'], encodings['attention_mask'])

# Move the model to the appropriate device (CPU or GPU)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
pretrained_model.to(device)

# Initialize the optimizer
optimizer = AdamW(pretrained_model.parameters(), lr=1e-5)

batch_size = 8
epochs = 3
import math

# Experiment with different chunk sizes
chunk_sizes_to_try = [200]  # Can add more sizes later

for chunk_size in chunk_sizes_to_try:
    for epoch in range(epochs):
        tqdm_dataloader = tqdm(DataLoader(dataset, batch_size=batch_size, shuffle=True), desc=f'Epoch {epoch + 1}/{epochs}')

        pretrained_model.train()
        for batch in tqdm_dataloader:
            input_ids, attention_mask = batch
            input_ids, attention_mask = input_ids.to(device), attention_mask.to(device)

            # Calculate number of chunks for current batch
            sequence_length = input_ids.size(1)  # Get actual sequence length
            num_chunks = math.ceil(sequence_length / chunk_size)

            for i in range(num_chunks):
                start_idx = i * chunk_size
                end_idx = min((i + 1) * chunk_size, sequence_length)  # Handle final chunk

                # Extract chunk data
                input_ids_chunk = input_ids[:, start_idx:end_idx]
                attention_mask_chunk = attention_mask[:, start_idx:end_idx]

                # Forward pass
                outputs = pretrained_model(
                    input_ids_chunk, attention_mask=attention_mask_chunk, labels=input_ids_chunk.reshape(-1)
                    )

                # Calculate loss
                loss = outputs.loss

                # Backward pass and optimization
                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                # Update progress bar
                tqdm_dataloader.set_postfix({'Loss': loss.item(), 'Chunk Size': chunk_size})

Some weights of the model checkpoint at sentence-transformers/all-mpnet-base-v2 were not used when initializing MPNetForMaskedLM: ['pooler.dense.weight', 'pooler.dense.bias']
- This IS expected if you are initializing MPNetForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing MPNetForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of MPNetForMaskedLM were not initialized from the model checkpoint at sentence-transformers/all-mpnet-base-v2 and are newly initialized: ['lm_head.bias', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias']
You should probably TRAIN this model on a down-stream task to be 

In [10]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [11]:
pretrained_model.save_pretrained('/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_base_v2')
tokenizer.save_pretrained('/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_base_v2')

('/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v2/tokenizer_config.json',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v2/special_tokens_map.json',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v2/vocab.txt',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v2/added_tokens.json',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v2/tokenizer.json')

In [ ]:
ls

fine_tuned_mpnet/     fine_tuned_resumes/  resumes6000.csv  the_resumesFirst.csv
fine_tuned_mpnet.zip  gdrive/              sample_data/


In [ ]:
pwd

'/content'

In [ ]:
cd /content

/content


In [ ]:
# Save the fine-tuned model
pretrained_model.save_pretrained('fine_tuned_mpnet_v1')
tokenizer.save_pretrained('fine_tuned_mpnet_v1')

('fine_tuned_mpnet_v1/tokenizer_config.json',
 'fine_tuned_mpnet_v1/special_tokens_map.json',
 'fine_tuned_mpnet_v1/vocab.txt',
 'fine_tuned_mpnet_v1/added_tokens.json',
 'fine_tuned_mpnet_v1/tokenizer.json')

In [ ]:
ls

fine_tuned_mpnet/     fine_tuned_mpnet.zip  gdrive/          sample_data/
fine_tuned_mpnet_v1/  fine_tuned_resumes/   resumes6000.csv  the_resumesFirst.csv


In [ ]:
pretrained_model.save_pretrained('/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1')
tokenizer.save_pretrained('/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1')


('/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1/tokenizer_config.json',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1/special_tokens_map.json',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1/vocab.txt',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1/added_tokens.json',
 '/content/gdrive/My Drive/Finetunedmodel/fine_tuned_mpnet_v1/tokenizer.json')

In [ ]:
from transformers import AutoTokenizer, AutoModelForMaskedLM

model= 'DeroG/mpnet_new'
tokenizer = AutoTokenizer.from_pretrained(model)
model = AutoModelForMaskedLM.from_pretrained(model)

In [ ]:
pip install  hnswlib

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for hnswlib: filename=hnswlib-0.8.0-cp310-cp310-linux_x86_64.whl size=2287618 sha256=f1176656b86f12880d251e5a85b8562e1be1a45d5618ecfa55f021001c459f48
  Stored in directory: /root/.cache/pip/wheels/af/a9/3e/3e5d59ee41664eb31a4e6de67d1846f86d16d93c45f277c4e7
Successfully built hnswlib


In [ ]:
pip install -U sentence-transformers

In [ ]:
import numpy as np
import pandas as pd
import re
# Download the NLTK stopwords
import nltk
nltk.download('punkt')
from nltk.corpus import stopwords
import pickle
import hnswlib
import sentence_transformers as st
from sentence_transformers import SentenceTransformer, util
import time
from tqdm import tqdm
import numpy as np
from math import ceil
from torch.nn import functional as F

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
resumes = pd.read_csv("/content/the_resumesFirst.csv")

In [ ]:
resumes.head(5)

Resume           Category
0  CESAR CABAL Financial Analyst ccabal43emailcom...  Digital Marketing
1  Selamawit Yemane Customer Service Manager sela...  Digital Marketing
2  DRISTAN ARTHUR BUDGET ANALYST CONTACT darthure...  Digital Marketing
3  BENTLI FALLA CAREER OBJECTIVE Creative and wit...  Digital Marketing
4  First Last Advertising Copy Writer Bay Area Ca...  Digital Marketing

In [ ]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [ ]:
Preprop_resumes = resumes["Resume"]

In [ ]:
# Function for cleaning and preprocessing the resume
def clean_resume(resume):
    if isinstance(resume, str):
        # Convert to lowercase
        resume = resume.lower()

        # Remove URLs, RT, cc, hashtags, mentions, non-ASCII characters, punctuation, and extra whitespace
        resume = re.sub('http\S+\s*|RT|cc|#\S+|@\S+|[^\x00-\x7f]|[^\w\s]', ' ', resume)
        resume = re.sub('\s+', ' ', resume).strip()

        # Tokenize the resume
        tokens = nltk.word_tokenize(resume)

        # Remove stopwords
        stop_words = set(stopwords.words('english'))
        tokens = [token for token in tokens if token.lower() not in stop_words]

        # Join the tokens back into a sentence
        preprocessed_resume = ' '.join(tokens)

        return preprocessed_resume
    else:
        return ''
# Applying the cleaning function to a Datasets
Preprop_resumes = Preprop_resumes.apply(lambda x: clean_resume(x))

In [ ]:
resumes = resumes["Resume"].tolist()

In [ ]:
Preprop_resumes = Preprop_resumes.tolist()

In [ ]:
from transformers import AutoTokenizer, AutoModelForMaskedLM

model= 'DeroG/mpnet_new'
tokenizer = AutoTokenizer.from_pretrained(model)
model = AutoModelForMaskedLM.from_pretrained(model)

In [ ]:
from transformers import AutoTokenizer
import torch
from tqdm import tqdm

def embed_resumes_with_progress(model, tokenizer, resumes, chunk_size=200):
    """
    Embeds a list of resumes using the SentenceTransformer model with chunking and progress bar.

    Args:
        model: The SentenceTransformer model.
        tokenizer: The Hugging Face Tokenizer for text pre-processing.
        resumes: A list of preprocessed resumes.
        chunk_size: Maximum number of tokens per chunk (default: 200).

    Returns:
        A numpy array containing the averaged embeddings for each resume.
    """
    resume_embeddings = []

    with tqdm(total=len(Preprop_resumes)) as pbar:
        for resume in Preprop_resumes:
            encoded_chunks = []
            chunks = [resume[i:i+chunk_size] for i in range(0, len(resume), chunk_size)]
            for chunk in chunks:
                encoded_chunk = tokenizer(chunk, padding=True, truncation=True, return_tensors="pt")
                with torch.no_grad():
                    chunk_embedding = model(**encoded_chunk)[0]
                    attention_mask = encoded_chunk["attention_mask"]
                    encoded_chunks.append(chunk_embedding)

            # Concatenate the encoded chunks
            concatenated_chunks = torch.cat(encoded_chunks, dim=1)
            resume_embedding = torch.mean(concatenated_chunks, dim=1)
            resume_embeddings.append(resume_embedding)

            pbar.update(1)

    return torch.cat(resume_embeddings)

In [ ]:
# Get resume embeddings
import torch
resume_embeddings = embed_resumes_with_progress(model, tokenizer, Preprop_resumes)

# Access individual embedding
first_resume_embedding = resume_embeddings[0]

100%|██████████| 9/9 [00:22<00:00,  2.51s/it]


In [ ]:
resume_embeddings.shape

torch.Size([9, 30527])

In [ ]:
job_description = """

Boyave
Full-Time
Description
Content Creator
Job brief
We are looking for a Content Creator to write and publish various types of pieces for our company’s web pages, like articles, ebooks and social media posts.
Content Creator responsibilities include producing marketing copy to advertise our products, writing blog posts about industry-related topics and promoting our content on social media. To be successful in this role, you should have experience with digital publishing and generating traffic and leads for new business. Please share samples of your work (portfolio or links to published articles) along with your application.
Ultimately, you will help us reach our target audience by delivering both useful and appealing online information about our company and products.
Responsibilities
•	Research industry-related topics
•	Prepare well-structured drafts using digital publishing platforms
•	Create and distribute marketing copy to advertise our company and products
•	Interview industry professionals and incorporate their views in blog posts
•	Edit and proofread written pieces before publication
•	Conduct keyword research and use SEO guidelines to optimize content
•	Promote content on social networks and monitor engagement (e.g. comments and shares)
•	Identify customers’ needs and recommend new topics
•	Coordinate with marketing and design teams to illustrate articles
•	Measure web traffic to content (e.g. conversion and bounce rates)
•	Update our websites as needed
Requirements and skills
•	Proven work experience as a Content Creator, Copywriter or similar role
•	Portfolio of published articles
•	Hands-on experience with Content Management Systems (e.g. WordPress)
•	Excellent writing and editing skills in English
•	An ability to fact-check long-form content pieces
•	Time-management skills
•	Familiarity with SEO
•	BSc in Marketing, English, Journalism or relevant field"""

In [ ]:
def clean_JD(JD):
  """
  Preprocesses the provided JD by:
    - Lowercasing all text
    - Removing punctuation
    - Removing stop words and punctuation and sympols
  """
  JD = JD.lower()
  JD = re.sub(r"[^\w\s]", "", JD)
  stop_words = stopwords.words("english")
  filtered_words = [word for word in JD.split() if word not in stop_words]
  cleaned_JD = " ".join(filtered_words)
  return  cleaned_JD

In [ ]:
cleaned_job_description = clean_JD(job_description)
print("Cleaned Job Description:", cleaned_job_description)

Cleaned Job Description: boyave fulltime description content creator job brief looking content creator write publish various types pieces companys web pages like articles ebooks social media posts content creator responsibilities include producing marketing copy advertise products writing blog posts industryrelated topics promoting content social media successful role experience digital publishing generating traffic leads new business please share samples work portfolio links published articles along application ultimately help us reach target audience delivering useful appealing online information company products responsibilities research industryrelated topics prepare wellstructured drafts using digital publishing platforms create distribute marketing copy advertise company products interview industry professionals incorporate views blog posts edit proofread written pieces publication conduct keyword research use seo guidelines optimize content promote content social networks monito

In [ ]:
from transformers import AutoTokenizer
from tqdm import tqdm


def embed_JD_with_progress(model, tokenizer, cleaned_job_description, chunk_size=200):
  """
  Embeds a job description using the SentenceTransformer model with chunking and progress bar.

  Args:
    model: The SentenceTransformer model.
    tokenizer: The Hugging Face Tokenizer for text pre-processing.
    cleaned_job_description: A preprocessed job description string.
    chunk_size: Maximum number of tokens per chunk (default: 200).

  Returns:
    A numpy array containing the embedding for the job description.
  """

  encoded_chunks = []
  chunks = [cleaned_job_description[i:i+chunk_size] for i in range(0, len(cleaned_job_description), chunk_size)]

  with tqdm(total=len(chunks), desc="Embedding Job Description") as pbar:
    for chunk in chunks:
      encoded_chunk = tokenizer(chunk, padding=True, truncation=True, return_tensors="pt")
      with torch.no_grad():
        chunk_embedding = model(**encoded_chunk)[0]
        attention_mask = encoded_chunk["attention_mask"]
        encoded_chunks.append(chunk_embedding)
      pbar.update(1)

  concatenated_chunks = torch.cat(encoded_chunks, dim=1)
  JD_embeddings = torch.mean(concatenated_chunks, dim=1)
  return JD_embeddings.cpu().numpy()


In [ ]:
# Get resume embeddings
import torch
JD_embeddings = embed_JD_with_progress(model, tokenizer, cleaned_job_description)

# Access individual embedding
first_JD_embedding = JD_embeddings[0]

Embedding Job Description: 100%|██████████| 8/8 [00:01<00:00,  4.79it/s]


In [ ]:
JD_embeddings.shape

(1, 30527)

In [ ]:
# Access individual embedding
first_JD_embedding = JD_embeddings[0]

In [ ]:
JD_embeddings

array([[ 2.4844365,  0.6637995,  7.125794 , ..., -1.8927242, -3.2216737,
         3.1794276]], dtype=float32)

In [ ]:
def similarity_percentage(similarity_score):
    if similarity_score < 0.2:
        return 0
    elif 0.2 <= similarity_score < 0.3:
        return similarity_score - 0.25
    elif 0.3 <= similarity_score < 0.4:
        return similarity_score - 0.23
    elif 0.4 <= similarity_score < 0.55:
        return similarity_score - 0.19
    elif 0.55 <= similarity_score < 0.65:
        return similarity_score - 0.14
    else:
      return similarity_score - 0.1

In [ ]:
def create_hnsw_index(embeddings, max_elements, ef_construction, M, ef):
    """
    Creates and initializes an HNSWLib index with the specified parameters.

    Args:
        embeddings: A list of embedding vectors.
        max_elements: Maximum number of elements to store in the index.
        ef_construction: Number of elements to consider during index construction.
        M: Maximum number of connections per node in the HNSW graph.
        ef: Number of elements to consider during search.

    Returns:
        An HNSWLib index object.
    """
    embedding_size = 30527
    index = hnswlib.Index(space='cosine', dim=embedding_size)
    index.init_index(max_elements, ef_construction, M)
    index.add_items(resume_embeddings, list(range(len(resume_embeddings))))
    index.set_ef(ef)
    return index

In [ ]:
# Define parameters for the index
max_elements = len(resume_embeddings)
ef_construction = 2000
M = 200
ef = 50
index = create_hnsw_index(resume_embeddings, max_elements, ef_construction, M, ef)
print("Corpus loaded with {} resumes / embeddings".format(len(resume_embeddings)))

# Retrieve resumes based on job description
take_k_hits = int(input("\nHow many top resumes do you want to be retrieved?\n\n"))

start_time = time.time()

resume_ids, dist = index.knn_query(JD_embeddings, take_k_hits)

# Calculate the similarity percentage and create a DataFrame
hits = [{'resume_id': id, 'Original_Score': 1 - score, 'Adjusted_Score': similarity_percentage(1 - score)} for id, score in zip(resume_ids[0], dist[0])]
hits = sorted(hits, key=lambda x: x['Adjusted_Score'], reverse=True)

end_time = time.time()

print("Results (after {:.3f} seconds):".format(end_time - start_time))

# Create a DataFrame with original and adjusted similarity scores
Resumeranking = pd.DataFrame(hits[:take_k_hits])
Resumeranking['Resumes'] = Resumeranking['resume_id'].map(lambda x: resumes[x])
Resumeranking = Resumeranking.drop(['resume_id'], axis=1)

# Convert Adjusted_Score to percentage format
Resumeranking['Original_Score'] = Resumeranking['Original_Score']
Resumeranking['Adjusted_Score'] = (Resumeranking['Adjusted_Score'] * 100).round(2)
Resumeranking['Adjusted_Score'] = Resumeranking['Adjusted_Score'].astype(str) + '%'

Resumeranking = Resumeranking[['Resumes', 'Original_Score', 'Adjusted_Score']]
Resumeranking

Corpus loaded with 9 resumes / embeddings

How many top resumes do you want to be retrieved?

9
Results (after 0.001 seconds):


Resumes  Original_Score  \
0  First Last Advertising Copy Writer Bay Area Ca...        0.980730   
1  BENTLI FALLA CAREER OBJECTIVE Creative and wit...        0.975105   
2  CESAR CABAL Financial Analyst ccabal43emailcom...        0.965548   
3  First Last Digital Marketing Manager WORK EXPE...        0.962464   
4  CHELSEY DEGA Marketing Manager chelseydegaemai...        0.959740   
5  Reinhardt Konig Human Resources Intern Driven ...        0.958368   
6  DRISTAN ARTHUR BUDGET ANALYST CONTACT darthure...        0.954127   
7  Selamawit Yemane Customer Service Manager sela...        0.953998   
8  OBJECTIVE To impart my knowledge in Veterinary...        0.931807   

  Adjusted_Score  
0         88.07%  
1         87.51%  
2         86.55%  
3         86.25%  
4         85.97%  
5         85.84%  
6         85.41%  
7          85.4%  
8         83.18%

In [ ]:
Resumeranking['Resumes'][0]

'First Last Advertising Copy Writer Bay Area California +1234456789 professionalemailresumewordedcom linkedincominusername Advertising Copy Writer with eight years experience working with art directors to craft meaningful content for marketing and sales campaigns for over 75 clients to meet their advertising goals Supervised up to 10 junior copywriters and interns to assist in sharpening their writing skills to create content that delights its readers Acquired the Most Impactful Omnichannel Campaign Award for creating a crossplatform campaign concept that garnered over two million YouTube views and increased the clients customer base by 47 RELEVANT WORK EXPERIENCE Resume Worded New York NY 2015 Present Advertising Copy Writer 2017 Present Ranked number one in the top quartile of 50 copywriters for productivity metrics The metrics included the number of ads completed as per the brief within the scheduled timeframe with the least rewrites Consulted with eight department leads including A

In [ ]:
Resumeranking['Resumes'][1]

'BENTLI FALLA CAREER OBJECTIVE Creative and witty media mind with 3 years in professional social Social Media Content media roles Looking to use my knowledgebase of platforms and Creator trends which have generated trending posts with over 2M+ views to create captivating content for a company like Blueland = bentlifallaemailcom 123 4567890 o 125 WORK EXPERIENCE Q Las Vegas NV ff LinkedIn Social Media Content Moderator Teleperformance September 2018 current Las Vegas NV EDUCATION e Navigated 5+ social media platforms posting and engaging with content to increase followers by 22 since 2019 BS Maintained strong grasp of English utilizing grammatically Communication accurate sentences to answer 100+ questions per shift University of Nevada Analyzed media inquiries and determined how to address August 2014 May 2018 customer issues within 2 hours of posting Updated knowledge of software systems including Office Achieved 55 WPM responding to chats in 45 seconds Las Vegas NV Social Media Manag

In [ ]:
Resumeranking['Resumes'][2]

'CESAR CABAL Financial Analyst ccabal43emailcom 123 4567890 Atlanta GA LinkedIn EDUCATION Masters Business Administration University of Georgia 2014 2016 Atlanta GA Bachelor of Science Finance University of Georgia 2010 2014 Atlanta GA SKILLS MS Excel Original Research Budget Development Project Management Data Analysis MA CAREER OBJECTIVE Detailoriented financial analyst with 6 years in quantitative statistical analysis budgeting accounting and forecasting Leveraging strong analytical skills to support operations through robust modeling to facilitate executivelevel decisionmaking and increase company revenue Quickly adapt to new technologies and attaining CPA licensure to become an indispensable asset to Logistics Property WORK EXPERIENCE Financial Analyst King Spalding October 2018 current Atlanta GA Update daily cash position through analysis investigation and reporting on key movements and trends in the PL lines Provide financial guidance to BusinessFunctions and assist in decision

In [ ]:
Resumeranking['Resumes'][4]

'CHELSEY DEGA Marketing Manager chelseydegaemailcom 123 4567890 Brooklyn NY LinkedIn EDUCATION BS Marketing University of Pittsburgh September 2010 April 2014 Pittsburgh PA SKILLS HubSpot Salesforce Microsoft Excel Word PowerPoint Paid Ads Facebook Google LinkedIn retargeting AB testing audience segmentation Google Analytics SEO WORK EXPERIENCE Marketing Manager HADASSAH May 2018 current New York NY Directed the launch of a campaign for a new platform resulting in revenue of $53M in the first year Created a holistic paid acquisition strategy ultimately leading to an ROI of 41 for every dollar spent Built out a culture of robust data collection and AB testing to iteratively improve campaign performance leading to an average improvement of 64 from campaign start to end Developed partnerships with higher education institutions in the US resulting in an incremental $74M in revenue Exceeded sales targets by 32 for the full year in 2019 Identified vendors who were underperforming leading to 

In [ ]:
Resumeranking['Resumes'][8]

'OBJECTIVE To impart my knowledge in Veterinary medicine and provide quality healthcare to animals My aim is to sustain animal life by administering immunization to guard them against diseases PERSONAL INFORMATION Brian Avelar 322 Dogwood Lane Tucson AZ 85712 7778844221 bavelarsampleresumenet Date of Birth May 6 1979 Place of Birth PA Citizenship American Gender Male PROFILE SUMMARY Knowledgeable in toxicology and laboratory animal medicines Great skills in interpreting animal behavior Pathology EDUCATION Doctor of Veterinary Medicine 2009 Polytechnic Institute of New York University Brooklyn BS in Biology 2006 Polytechnic Institute of New York University Brooklyn EMPLOYMENT HISTORY Pharmaceutical Veterinarian 2007 Present AstraZeneca Pharmaceuticals LP Wilmington DE Responsibilities Administered immunization to animals to protect them from diseases Studied cause of animal diseases Reviewed the list of raw materials to be used and mixed in the vaccine Tested efficacy and effectiveness 